<p style="font-family: Arial; font-size:2.75em;color:blue; font-style:bold"><br>
Projet 6 :<br><br>
Catégorisez automatiquement des questions<br><br>
</p><br>

* **Data Source / Data Source :** 
    - Data :
        - Outils d'extraction de data : https://data.stackexchange.com/stackoverflow
        - Script : https://github.com/EricJacquesPro/TextCategorization/blob/master/SQL/ExtractionDonnees.sql
    - Source Python : https://github.com/EricJacquesPro/TextCategorization
* **Description / Description : ** Projet 6 de la formation Data Scientist Proposée par OpenClassroom
    - Analyse
    - Entrainement
* **Auteur / Author : ** Eric JACQUES 
* **Date : ** 19/07/2020 

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
I - Sélection des datas entrantes</p>

Stack overfloaw met a disposition un outils en ligne permettant d'extraire le contenu de post diffusés sur le site internet.
(https://data.stackexchange.com/stackoverflow)<br>
En se basant sur la structure de la base de données(https://i.stack.imgur.com/JZHsN.png), il en ressort des données (tables) plus intéressantes que d'autres : Post, type de post, Tag, tags des posts <br>
Pour notre cas, tous les posts ne sont pas intéressants : Supprimé, score null, sans réponse, type de post....<br>
<br>
Parmis les posts, les données les plus explicites qui permettent de connaitre leurs sujets sont le body.<br>
<br>
Script téléchargeable sur https://github.com/EricJacquesPro/TextCategorization/blob/master/SQL/ExtractionDonnees.sql



<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
II - Data cleaning & preprocessing</p>

In [1]:
import sys
import os
import numpy as np
import pandas as pd
sys.path.insert(0, './Python/')

In [2]:
'''
python class for the data engineering (reading, cleaning, training...)
localised in ./Python
'''
from tagText import TagText 

C:\Users\naru_\Anaconda3\lib\site-packages\gensim\utils.py:1209: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [3]:
cluster_number_min = 2
cluster_number_max = 10
cluster_number_step = 2

tagText = TagText()
print(tagText.urlDirectory)#folder for cvs file generated by SQL query (cf. I) 
print(tagText.fileName)#name of the cvs file generated by SQL query (cf. I)
tagText.nombre_post_entree = 50000
tagText.precision = 50000
data_question = tagText.read_source()
data_question.head()

Data/
QuestionVsTags.csv


body  \
0  <p>Here is a piece of C++ code that shows some...   
1  <p>I accidentally committed the wrong files to...   
2  <p>I want to delete a branch both locally and ...   
3  <p>What are the differences between <code>git ...   
4  <p>What is the use of the <code>yield</code> k...   

                                               title  \
0  Why is processing a sorted array faster than p...   
1  How do I undo the most recent local commits in...   
2  How do I delete a Git branch locally and remot...   
3  What is the difference between 'git pull' and ...   
4                  What does the "yield" keyword do?   

                                                tags  \
0  <java><c++><performance><optimization><branch-...   
1  <git><version-control><git-commit><undo><pre-c...   
2  <git><version-control><git-branch><git-push><g...   
3        <git><version-control><git-pull><git-fetch>   
4    <python><iterator><generator><yield><coroutine>   

                         SelectedTags      Name  
0  java,c++,performance,optimization,  Question  
1                git,version-control,  Question  
2                git,version-control,  Question  
3                git,version-control,  Question  
4                    python,iterator,  Question

In [4]:
data_question.describe().T

count unique                                                top  \
body          50000  50000  <p><strong>I don't know when attribute should ...   
title         50000  49998                              Autocompletion in Vim   
tags          50000  35459                                              <git>   
SelectedTags  50000  15589                                               git,   
Name          50000      1                                           Question   

               freq  
body              1  
title             2  
tags            410  
SelectedTags   1225  
Name          50000

In [5]:
print(tagText.stopwords)
'''Stop word issu to nltk.corpus'''

{'to', 'were', 'whom', "don't", 'than', "she's", 'have', 'out', 'theirs', 'himself', 'was', 'or', 'below', 'couldn', 'there', 'if', 'few', 'wasn', 'how', 'your', 'mightn', "shouldn't", 'isn', 'myself', 'of', 'these', 'yourselves', "shan't", "didn't", 'but', 'here', 'needn', "wouldn't", 'itself', "hasn't", "weren't", 'then', "it's", 'and', 'he', "you'll", 'hers', 'they', 'hasn', "won't", 'o', 'over', 'for', 'which', "you've", 're', 'ourselves', 'its', 'further', 'why', 'doesn', 'under', "wasn't", 'it', 'do', 'against', 'a', 'haven', 'what', 'i', 'you', 'on', 'same', 'in', 'did', 'an', 'by', 'my', 'after', 'be', 'any', "you'd", 'between', 'are', 'having', 'before', 'again', 'off', 'we', 'so', "hadn't", 'is', 'doing', "aren't", 'am', 'me', 'had', 'the', 've', 'don', 'both', 'such', 'while', 'm', 'd', 'about', 'where', 'their', 'can', 'that', 'll', 'who', "haven't", 'not', "mightn't", 'above', 'herself', 'during', 'themselves', 'aren', 'her', 'yours', 'yourself', 'has', 'this', 'y', 'just'

'Stop word issu to nltk.corpus'

In [6]:
data_question['body'][1:9]

1    <p>I accidentally committed the wrong files to...
2    <p>I want to delete a branch both locally and ...
3    <p>What are the differences between <code>git ...
4    <p>What is the use of the <code>yield</code> k...
5    <p>I've been messing around with <a href="http...
6    <p>I mistakenly added files to Git using the c...
7    <p>After reading <a href="http://groups.google...
8    <p>I don't want to rename a remote branch, as ...
Name: body, dtype: object

<p style="font-family: Arial; color:red; font-style:bold">
Deleting nltk stopwords is not enough because there are lot of html and punctuation caracters
</p>

In [7]:
data_preprocessed = data_question['body'].apply(tagText.preprocessing)
print(data_preprocessed[1:9])

1    accidentally committed wrong files git pushed ...
2    want delete branch locally remotely failed att...
3                       differences git pull git fetch
4    use yield keyword python do example im trying ...
5    ive messing around json time pushing text hurt...
6    mistakenly added files git using command git a...
7    reading hidden features dark corners cstl comp...
8    want rename remote branch described rename mas...
Name: body, dtype: object


In [8]:
data_question.head()

body  \
0  <p>Here is a piece of C++ code that shows some...   
1  <p>I accidentally committed the wrong files to...   
2  <p>I want to delete a branch both locally and ...   
3  <p>What are the differences between <code>git ...   
4  <p>What is the use of the <code>yield</code> k...   

                                               title  \
0  Why is processing a sorted array faster than p...   
1  How do I undo the most recent local commits in...   
2  How do I delete a Git branch locally and remot...   
3  What is the difference between 'git pull' and ...   
4                  What does the "yield" keyword do?   

                                                tags  \
0  <java><c++><performance><optimization><branch-...   
1  <git><version-control><git-commit><undo><pre-c...   
2  <git><version-control><git-branch><git-push><g...   
3        <git><version-control><git-pull><git-fetch>   
4    <python><iterator><generator><yield><coroutine>   

                         SelectedTags      Name  
0  java,c++,performance,optimization,  Question  
1                git,version-control,  Question  
2                git,version-control,  Question  
3                git,version-control,  Question  
4                    python,iterator,  Question

In [9]:
data_preprocessed.describe()

count                                                 50000
unique                                                50000
top       newbie gradle artifactory want upload jar file...
freq                                                      1
Name: body, dtype: object

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III - Data - Bag of words</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.1 - Data - Bag of words - most frequent data</p>

In [10]:
import nltk
print(nltk.word_tokenize(data_preprocessed[0])[0:10])
print(nltk.tokenize.WhitespaceTokenizer().tokenize(data_preprocessed[0])[0:10])
# Tokenize using Punctuations
print(nltk.tokenize.WordPunctTokenizer().tokenize(data_preprocessed[0])[0:10])
print(nltk.tokenize.TreebankWordTokenizer().tokenize(data_preprocessed[0])[0:10])

['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.2 - Data - Bag of words - Nb of occurence</p>

In [11]:
import nltk
from collections import defaultdict
    
corpora = defaultdict(list)
        
tokenizer = nltk.RegexpTokenizer(r'\w+')
for id, row in data_preprocessed.iteritems():
    for word in tokenizer.tokenize(row):
        if not word in corpora :
            corpora[word] = 0
        #print(word)
        corpora[word] += 1

In [12]:
import matplotlib.pyplot as plt
minimum_count = 2#200
def count_word_occurencies(df):
        corpora = defaultdict(list)                
        tokenizer = nltk.RegexpTokenizer(r'\w+')
        for id, row in df.iteritems():
            for word in tokenizer.tokenize(row):
                if not word in corpora :
                    corpora[word] = 0
                #print(word)
                corpora[word] += 1
        corpora = dict((k, v) for k, v in corpora.items() if ((v > minimum_count)))
        sorted(corpora)
        print('''test0''')
        print(corpora)
        corpora = dict((k, v) for k, v in corpora.items() if ((v > 1)))
        print('''test''')
        print(corpora)
        return (sorted(corpora.items(), reverse=True,  key=lambda x: x[1]))

In [13]:
dico = count_word_occurencies(data_preprocessed)

test0
{'l4': 7, 'printfp': 3, 'invalidation': 5, 'getchilditem': 16, 'insection0': 4, 'listbook': 4, 'secure': 179, 'ourselves': 3, '0407': 4, 'hope': 311, 'stripped': 33, 'paradigm': 48, 'allotherstuffdbcontext': 3, 'using': 18115, 'wfemale': 3, 'windowmanager': 10, 'arrayssort': 4, 'passbyreference': 6, 'apples': 101, 'androidlayoutweight85': 7, 'svn': 494, 'willset': 3, '19710': 3, '382008': 8, 'pck': 3, '0111': 5, 'defaulttablemodel': 7, 'safevarargs': 3, '938': 3, 'ondraweropenedview': 5, 'testone': 6, 'songname': 3, 'idabcdefg': 3, 'superonpostcreatesavedinstancestate': 3, '000': 356, 'ggsave': 7, 'countyid': 4, 'jarowinkler': 5, 'daemons': 12, 'rootsshidrsa': 6, 'docx': 4, 'modally': 13, 'proxypreservehost': 5, 'iso8601': 7, 'durable': 8, 'halt': 22, 'margintop': 53, 'collectionsemptylist': 7, 'logidebug': 4, 'pinterest': 15, 'canexecute': 6, 'psycopg': 3, 'landscape': 105, 'propose': 10, 'mechanisms': 28, 'dict1': 5, 'assumptions': 38, 'slength': 16, 'bethesda': 3, 'classtabpan

In [14]:
print(len(dico))
dico

43587


[('like', 20054),
 ('using', 18115),
 ('im', 17253),
 ('use', 16179),
 ('code', 15024),
 ('want', 14907),
 ('get', 14492),
 ('way', 14146),
 ('file', 13511),
 ('would', 13404),
 ('new', 12705),
 ('error', 11991),
 ('1', 11312),
 ('this', 11309),
 ('string', 11002),
 ('one', 10960),
 ('class', 10443),
 ('return', 9786),
 ('function', 9664),
 ('public', 9638),
 ('need', 8528),
 ('know', 8500),
 ('0', 8245),
 ('following', 7905),
 ('2', 7764),
 ('example', 7619),
 ('ive', 7603),
 ('something', 7581),
 ('set', 7335),
 ('data', 7304),
 ('it', 7254),
 ('work', 6980),
 ('c', 6956),
 ('id', 6955),
 ('method', 6864),
 ('var', 6830),
 ('value', 6811),
 ('name', 6450),
 ('div', 6255),
 ('trying', 6230),
 ('find', 6198),
 ('also', 6021),
 ('object', 5959),
 ('int', 5873),
 ('tried', 5791),
 ('could', 5689),
 ('git', 5689),
 ('line', 5676),
 ('type', 5580),
 ('question', 5472),
 ('run', 5423),
 ('files', 5398),
 ('time', 5395),
 ('make', 5299),
 ('list', 5164),
 ('see', 5162),
 ('problem', 5140),
 

In [15]:
print(tagText.count_word_occurencies(data_preprocessed))

[('like', 20054), ('using', 18115), ('im', 17253), ('use', 16179), ('code', 15024), ('want', 14907), ('get', 14492), ('way', 14146), ('file', 13511), ('would', 13404), ('new', 12705), ('error', 11991), ('1', 11312), ('this', 11309), ('string', 11002), ('one', 10960), ('class', 10443), ('return', 9786), ('function', 9664), ('public', 9638), ('need', 8528), ('know', 8500), ('0', 8245), ('following', 7905), ('2', 7764), ('example', 7619), ('ive', 7603), ('something', 7581), ('set', 7335), ('data', 7304), ('it', 7254), ('work', 6980), ('c', 6956), ('id', 6955), ('method', 6864), ('var', 6830), ('value', 6811), ('name', 6450), ('div', 6255), ('trying', 6230), ('find', 6198), ('also', 6021), ('object', 5959), ('int', 5873), ('tried', 5791), ('git', 5689), ('could', 5689), ('line', 5676), ('type', 5580), ('question', 5472), ('run', 5423), ('files', 5398), ('time', 5395), ('make', 5299), ('list', 5164), ('see', 5162), ('problem', 5140), ('user', 5008), ('3', 4935), ('two', 4926), ('project', 4

<p style="font-family: Arial; color:red; font-style:bold">
Generating a dictionary of the most frequent terms is not interesting because we find a lot of words without great interest
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.2 - Data - Bag of words - TF-IDF</p>

In [16]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer

stemmer = nltk.stem.porter.PorterStemmer()
stopword = nltk.corpus.stopwords.words('english')

#X = data_preprocessed.unique()
X = data_preprocessed[0:9].unique()

def stem_and_filter(doc):
    tokens = [stemmer.stem(w) for w in analyzer(doc)]
    return [token for token in tokens if token.isalpha()]

analyzer = TfidfVectorizer().build_analyzer()
cv = TfidfVectorizer(lowercase=True, stop_words="english", analyzer=stem_and_filter, min_df=0.00, max_df=0.3)  # we remove words if it appears in more than 30 % of the corpus (not found stopwords like Box, Christmas and so on)
word_count_vector = cv.fit_transform(X)
print("TF_IDF_matrix :", word_count_vector.shape, "of", word_count_vector.dtype)
tfidf_transformer=TfidfTransformer(smooth_idf=True,use_idf=True)
tfidf_transformer.fit(word_count_vector)
# print idf values
df_idf = pd.DataFrame(tfidf_transformer.idf_, index=cv.get_feature_names(),columns=["tf_idf_weights"])
 
# sort ascending
df_idf.sort_values(by=['tf_idf_weights'])


TF_IDF_matrix : (9, 247) of float64


tf_idf_weights
file                              2.203973
time                              2.203973
int                               2.203973
branch                            2.203973
start                             2.203973
thi                               2.203973
return                            2.203973
tri                               2.203973
piec                              2.203973
repositori                        2.203973
id                                2.203973
pull                              2.203973
remot                             2.203973
commit                            2.203973
compil                            2.203973
result                            2.203973
standard                          2.203973
differ                            2.203973
undo                              2.203973
similar                           2.203973
yet                               2.203973
well                              2.203973
want                              2.203973
new                               2.203973
complet                           2.203973
main                              2.203973
run                               2.203973
use                               2.203973
selfmedian                        2.609438
read                              2.609438
...                                    ...
iostream                          2.609438
initi                             2.609438
exampl                            2.609438
extrem                            2.609438
fail                              2.609438
faster                            2.609438
featur                            2.609438
fetch                             2.609438
first                             2.609438
follow                            2.609438
found                             2.609438
from                              2.609438
gather                            2.609438
gcc                               2.609438
intarrays                         2.609438
gener                             2.609438
getchildcandidatesself            2.609438
githubcomgitusergitproject        2.609438
go                                2.609438
goe                               2.609438
great                             2.609438
happen                            2.609438
here                              2.609438
hidden                            2.609438
hurt                              2.609438
im                                2.609438
import                            2.609438
independ                          2.609438
getchildcandid                    2.609438
yield                             2.609438

[247 rows x 1 columns]

<p style="font-family: Arial; color:red; font-style:bold">
The words proposed following the TF-IDF generation seem more interesting than the list of the most frequent words.
We will favor TF-IDF for the rest.
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV - Data - Tag genetaor </p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.1 - Data - Tag generator - Unsupervised - By nb of occurence</p>

In [17]:
dict_tag = count_word_occurencies(data_preprocessed)
dict_tag = str(dict_tag)
dict_tag


test0
{'l4': 7, 'printfp': 3, 'invalidation': 5, 'getchilditem': 16, 'insection0': 4, 'listbook': 4, 'secure': 179, 'ourselves': 3, '0407': 4, 'hope': 311, 'stripped': 33, 'paradigm': 48, 'allotherstuffdbcontext': 3, 'using': 18115, 'wfemale': 3, 'windowmanager': 10, 'arrayssort': 4, 'passbyreference': 6, 'apples': 101, 'androidlayoutweight85': 7, 'svn': 494, 'willset': 3, '19710': 3, '382008': 8, 'pck': 3, '0111': 5, 'defaulttablemodel': 7, 'safevarargs': 3, '938': 3, 'ondraweropenedview': 5, 'testone': 6, 'songname': 3, 'idabcdefg': 3, 'superonpostcreatesavedinstancestate': 3, '000': 356, 'ggsave': 7, 'countyid': 4, 'jarowinkler': 5, 'daemons': 12, 'rootsshidrsa': 6, 'docx': 4, 'modally': 13, 'proxypreservehost': 5, 'iso8601': 7, 'durable': 8, 'halt': 22, 'margintop': 53, 'collectionsemptylist': 7, 'logidebug': 4, 'pinterest': 15, 'canexecute': 6, 'psycopg': 3, 'landscape': 105, 'propose': 10, 'mechanisms': 28, 'dict1': 5, 'assumptions': 38, 'slength': 16, 'bethesda': 3, 'classtabpan

"[('like', 20054), ('using', 18115), ('im', 17253), ('use', 16179), ('code', 15024), ('want', 14907), ('get', 14492), ('way', 14146), ('file', 13511), ('would', 13404), ('new', 12705), ('error', 11991), ('1', 11312), ('this', 11309), ('string', 11002), ('one', 10960), ('class', 10443), ('return', 9786), ('function', 9664), ('public', 9638), ('need', 8528), ('know', 8500), ('0', 8245), ('following', 7905), ('2', 7764), ('example', 7619), ('ive', 7603), ('something', 7581), ('set', 7335), ('data', 7304), ('it', 7254), ('work', 6980), ('c', 6956), ('id', 6955), ('method', 6864), ('var', 6830), ('value', 6811), ('name', 6450), ('div', 6255), ('trying', 6230), ('find', 6198), ('also', 6021), ('object', 5959), ('int', 5873), ('tried', 5791), ('could', 5689), ('git', 5689), ('line', 5676), ('type', 5580), ('question', 5472), ('run', 5423), ('files', 5398), ('time', 5395), ('make', 5299), ('list', 5164), ('see', 5162), ('problem', 5140), ('user', 5008), ('3', 4935), ('two', 4926), ('project', 

In [18]:
def unsupervised_tag(dict_word_key, new_question, number_max_tag):
    tags = [word for word in new_question.split() if (word in dict_word_key)]
    return tags[0:number_max_tag]

print(unsupervised_tag(dict_tag, "How save my code source with soft like git", 20))
print(unsupervised_tag(dict_tag, "How save my code source with soft like like git", 2))
#for word in "like git branche totot, test".split() if (word in dict_word_key)

['save', 'my', 'code', 'source', 'with', 'soft', 'like', 'git']
['save', 'my']


In [19]:
tagText.unsupervised_tag(dict_tag, "How save my code source with soft like git", 2)

['save', 'my']

<p style="font-family: Arial; color:red; font-style:bold">
Not interesting because we receive words without interest
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.2-a - Data - Tag generator - Unsupervised - LDA</p>

<p style="font-family: Arial; color:red; font-style:bold">
For more detals about LDA and to generate lda.joblib, please, see the notebook Projet_V2_LDA-v2-Detals.ipynb
</p>

In [20]:
'''
If you want to generate lda model
'''
lda_load, df_topic_keywords_load, tf_vectorizer_load, clf_load = tagText.lda_prepare_tag_and_save_V2(data_preprocessed, data_question['SelectedTags'], 10)


In [21]:

print('Topics From working class : ')
tagText.display_topics(lda_load, tf_vectorizer_load.get_feature_names(), 10)


Topics From working class : 
Topic : 0 :
install npm pip gem installed generator virtualenv sudo package timezone
Topic : 1 :
ding colored lia androidlayoutwidthmatchparent longitude axis latitude flex spinner color
Topic : 2 :
git commit branch repository master remote changes commits github repo
Topic : 3 :
table column sql select columns query unsigned dataframe join rows
Topic : 4 :
orgs elaborate ad timespan rewriterule vars www viceversa grammar stringsplit
Topic : 5 :
certificate https blah stringbuilder iboutlet httpclient ssl makefile keychain openssl
Topic : 6 :
div html css input width height button text ul tr
Topic : 7 :
bla flask tuples s2 s1 mvn aws s3 memorystream webservice
Topic : 8 :
like using im want way use file string code new
Topic : 9 :
df plot matplotlib myobject underscore finds legend eax imagemagick np


In [22]:
message = 'I want to create a web site in html'
print(message)

print(tagText.lda_predict_V2(message, tf_vectorizer_load, lda_load, clf_load, df_topic_keywords_load ))

I want to create a web site in html
['generics', 'mongodb', 'tsql', 'function', 'cocoa-touch']


<p style="font-family: Arial; color:red; font-style:bold">
LDA prediction seems to be interesting
</p>

In [23]:
lda_load, df_topic_keywords_load, tf_vectorizer_load, clf_load = tagText.lda_prepare_tag_and_save_V2(data_preprocessed, data_question['SelectedTags'], 32)

print(tagText.lda_predict_V2('git est un outils de code source. C\'est bien', tf_vectorizer_load, lda_load, clf_load, df_topic_keywords_load ,10))


['command-line', 'go', 'numpy', 'pip', 'cocoa-touch', 'linq', 'docker', 'maven', 'ggplot2', 'file']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.3 - Data - Tag generator - Supervised</p>

In [24]:
classifier, tags = tagText.supervised_prepare_tagV2(data_preprocessed, data_question['SelectedTags'])
message = 'git est un outils de code source. C\'est bien'

print(message)

print(tagText.supervised_predict(message, classifier, tags, 10))

score 1 occurence 2.96
score 5 occurences 0.08
git est un outils de code source. C'est bien
['google-chrome', 'debugging', 'ajax', 'python-3.x', 'dataframe', 'scala', 'go', 'oop', 'intellij-idea', 'linq']


In [25]:
print(tagText.supervised_predict(data_preprocessed[0], classifier, tags ))

['exception', 'python-3.x', 'debugging', 'ajax', 'dataframe']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
V - Resultat</p>

In [26]:

import numpy as np
import nltk
import pandas as pd
import os
import sys

sys.path.insert(0, './Python/')

from tagText import TagText


tagText = TagText()
print(tagText.urlDirectory)
print(tagText.fileName)
nombre_post_entree = 50000
precision = 50000
tagText.nombre_post_entree = nombre_post_entree
tagText.precision = precision
nombre_suggestion = 6

def supervisedTagPurposer():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'false', 'false')

def supervisedTagPurposerAndReload():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'true', 'false')

def supervisedTagPurposerAndReloadAndSave():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagLDAPurposer():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'false', 'false')

def tagLDAPurposerAndReload():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'true', 'false')

def tagLDAPurposerAndReloadAndSave():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagPurposer(mode, message, reload, saveModel):
    if mode.lower() == 'supervised':
        return superviedTagPurposerFromMessage(message, reload.lower(), saveModel.lower())
    if mode.lower() == 'lda':
        return unsuperviedTagTFIDFPurposerFromMessage(mode.lower(), message, reload.lower(), saveModel.lower())
    return '/i\\Mode indefined/i\\'

def superviedTagPurposerFromMessage(message, reload, saveModel):
    tagText = TagText()
    tagText.nombre_post_entree = nombre_post_entree
    tagText.precision = precision
    tags = ''
    if reload.lower() == 'true':
        data_question = tagText.read_source()
        data_preprocessed = data_question['body'].apply(tagText.preprocessing)
        if saveModel.lower() == 'true':
            classifier, tags_existants = tagText.supervised_prepare_tag_and_save(data_preprocessed, data_question['SelectedTags'])
            tags = tagText.supervised_predict(message, classifier, tags_existants)
        else :
            classifier, tags_existants = tagText.supervised_prepare_tagV2(data_preprocessed, data_question['SelectedTags'])
            tags = tagText.supervised_predict(message, classifier, tags_existants)
    else:
        classifier, tags_existants = tagText.supervised_prepare_tag_load()
        tags = tagText.supervised_predict(message, classifier, tags_existants)
    return tags

def unsuperviedTagTFIDFPurposerFromMessage(option, message, reloadModel, saveModel):
    tagText = TagText()
    tagText.nombre_post_entree = nombre_post_entree
    tagText.precision = precision
    tags = ''
    if option.lower() != 'lda':
        return '/i\\Mode undefined/i\\'
    if reloadModel.lower() == 'true':
        data_question = tagText.read_source()
        data_preprocessed = data_question['body'].apply(tagText.preprocessing)
        if option.lower() == 'lda':
            if saveModel.lower() == 'true':
                lda_load, df_topic_keywords_load, tf_vectorizer_load, clf_load = tagText.lda_prepare_tag_and_save_V2(
                    data_preprocessed, 
                    data_question['SelectedTags'],
                    no_tropics = 10
                )
                tags = tagText.lda_predict_V2(message, tf_vectorizer_load, lda_load, clf_load, df_topic_keywords_load, nombre_suggestion)
            else:
                lda_tagText_2, df_topic_keywords_2, tf_vectorizer_2, clf_2 = tagText.lda_prepare_tag_V2(
                    data=data_preprocessed,
                    tag=data_question['SelectedTags'],
                    no_tropics=10
                )
                tags = tagText.lda_predict_V2(message, tf_vectorizer_2, lda_tagText_2, clf_2, df_topic_keywords_2, nombre_suggestion)
    else:
        lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, clf = tagText.lda_prepare_tag_V2_load()
        tags = tagText.lda_predict_V2(message, tf_vectorizer_tagText, lda_tagText, clf, df_topic_keywords_tagText, nombre_suggestion)
    return tags


Data/
QuestionVsTags.csv


In [27]:
supervisedTagPurposerAndReloadAndSave()

score 1 occurence 2.96
score 5 occurences 0.08


"['version-control', 'debugging', 'python-3.x', 'ajax', 'google-chrome']"

In [28]:
supervisedTagPurposerAndReload()

score 1 occurence 2.96
score 5 occurences 0.08


"['version-control', 'debugging', 'python-3.x', 'ajax', 'google-chrome']"

In [29]:
supervisedTagPurposer()

"['version-control', 'debugging', 'python-3.x', 'ajax', 'google-chrome']"

In [30]:
tagLDAPurposerAndReloadAndSave()

"['npm', 'visual-studio', 'android-viewpager', 'layout', 'command-line', 'xcode']"

In [31]:
tagLDAPurposerAndReload()

"['npm', 'visual-studio', 'android-viewpager', 'layout', 'command-line', 'xcode']"

In [32]:
tagLDAPurposer()

"['npm', 'visual-studio', 'android-viewpager', 'layout', 'command-line', 'xcode']"

Une API :  https://ejacques.pythonanywhere.com/apiTagGenerator/

Un depot GIT : https://github.com/EricJacquesPro/TextCategorization/